In [1]:
import phylustrator.ale_parser as alep

# Replace with your actual file path
ale_file = "../data/K00319.ale.uml_rec" 
data = alep.parse_ale_file(ale_file)

print(f"Loaded Species Tree with {len(data.species_tree)} nodes.")
print(f"Log Likelihood: {data.log_likelihood}")
print(f"Rates: {data.rates}")
print(f"Found {len(data.gene_trees)} reconciled gene trees.")



Loaded Species Tree with 2852 nodes.
Log Likelihood: -1136.19
Rates: {'Duplications': 0.154163, 'Transfers': 0.0712109, 'Losses': 0.643975}
Found 100 reconciled gene trees.


In [2]:
import phylustrator as ph
import phylustrator.ale_parser as alep
import pandas as pd

# 1. Parse ALE Data
# ---------------------------------------------------------
ale_file = "../data/K00319.ale.uml_rec"
data = alep.parse_ale_file(ale_file)

t = data.species_tree

# 2. Convert to Ultrametric (Align Tips)
# ---------------------------------------------------------
# This forces all leaves to be equidistant from the root
try:
    t.convert_to_ultrametric()
except ValueError:
    print("Warning: Tree could not be perfectly converted (possibly due to 0-length branches).")

# 3. Setup Style (Specific Dimensions)
# ---------------------------------------------------------
style = ph.TreeStyle(
    radius=350,          # Requested Radius
    width=800,           # Canvas Width
    height=800,          # Canvas Height
    branch_size=1,       # Requested Branch Width
    node_size=0,         # Hide Nodes
    leaf_color="none"    # Hide default leaf dots
)

drawer = ph.TreeDrawer(t, style=style)

# 4. Color Logic: Red if Origination > 0
# ---------------------------------------------------------
branch2color = {}

# Convert branch_stats to a dictionary for faster lookup: { 'S_node_name': {row_data} }
stats_map = data.branch_stats.set_index("name").to_dict(orient="index")

for n in t.traverse():
    if n.is_root():
        branch2color[n] = "black"
        continue
        
    # Look up node name in stats
    # Note: ALE internal nodes often have integer names ('1', '2') which match S_node
    node_data = stats_map.get(n.name)
    
    if node_data:
        originations = node_data.get("Originations", 0.0)
        
        # Check condition
        if originations > 0:
            branch2color[n] = "#D62728" # Red
        else:
            branch2color[n] = "black"
    else:
        branch2color[n] = "black" # Default if no data found

# 5. Draw the Tree
# ---------------------------------------------------------
drawer.draw(branch2color=branch2color)

# 6. Add "Copies" Ring (Presence/Absence)
# ---------------------------------------------------------
# Extract 'copies' data for leaves only
heatmap_data = {}
for l in t.get_leaves():
    node_data = stats_map.get(l.name)
    if node_data:
        heatmap_data[l.name] = {"Copies": node_data.get("copies", 0.0)}

# Color Mapper: Dark Blue if present (> 0.5), Light Grey if absent
def copy_cmap(val):
    if val >= 0.5: return "#1F77B4" # Blue
    return "#F0F0F0" # Very light grey

# Add the ring just outside the radius (350 + 5 padding)
drawer.add_heatmap_matrix(
    heatmap_data, 
    columns=["Copies"], 
    start_radius=355, 
    ring_width=20, 
    gap=0, 
    cmap=copy_cmap,
    border="none"
)

# 7. Display
# ---------------------------------------------------------
# Save both formats just in case
drawer.save_figure("ale_originations.svg")
display(drawer.d)

Figure saved to ale_originations.svg


In [3]:
transfers = alep.parse_uts_file("../data/K00319.ale.uTs") # Ensure this file exists!

In [6]:
import phylustrator as ph
import phylustrator.ale_parser as alep

# 1. Parse Files
# -----------------------------
ale_data = alep.parse_ale_file("../data/K00319.ale.uml_rec")
transfers = alep.parse_uts_file("../data/K00319.ale.uTs") # Ensure this file exists!
#transfers = [{"from": "ARC_0002", "to":"ARC_0495", "freq":10}]
t = ale_data.species_tree
t.convert_to_ultrametric()

# 2. Setup Plot
# -----------------------------
style = ph.TreeStyle(
    radius=400, 
    width=1000, 
    height=1000,
    node_size=0,
    branch_size=1.5,
    leaf_size=0,
)
drawer = ph.TreeDrawer(t, style=style)

# 3. Draw Tree (Base)
# -----------------------------
# (Optional: Add your origination color logic here from previous step)
drawer.draw()

# 4. Add Transfer Links
# -----------------------------
# min_freq=0.01: Hides very rare transfers to reduce clutter
# opacity_scale=2.0: Makes the lines more visible
# curve_factor=0.5: Standard "swoop" towards center
drawer.add_transfer_links(
    transfers, 
    color="#FF8C00",    # Dark Orange
    min_freq=0.01, 
    opacity_scale=5.0, 
    curve_factor=0.1,
    gradient_colors=("gold", "darkred"),
)

# 5. Add Decorations
# -----------------------------
#drawer.add_leaf_names(padding=20)
drawer.add_text("Gene Transfer Network", x=-450, y=-450, size=18, font_weight="bold", anchor="start")

# Save
drawer.save_figure("ale_transfers.svg")
display(drawer.d)

Figure saved to ale_transfers.svg
